In [1]:
import os
import pandas as pd
import numpy as np
import datetime
import matplotlib.pyplot as plt
import scipy.stats
import pymannkendall as mk
import math
from scipy.interpolate import make_interp_spline

## Data Audit

In [2]:
df_mastertable = pd.read_csv('../data/performance_data(2021-2023Jan).csv', low_memory = False)

In [3]:
df_mastertable.head(5)

Week Skill Case Channel  Resolution Rate  NETRT SLA  ResRec SLA  \
0  06-Feb-21   SBG         CHAT         0.333333        NaN         NaN   
1  20-Feb-21   SBG         CHAT         0.666667        NaN         NaN   
2  27-Feb-21   SBG         CHAT         0.666667        NaN         NaN   
3  06-Mar-21   SBG         CHAT         0.576923        NaN         NaN   
4  13-Mar-21   SBG         CHAT         0.500000        NaN         NaN   

   Chat SLA  Email SLA  Actual AHT  emp_id  
0       NaN        NaN         NaN     269  
1       NaN        NaN         NaN     269  
2       NaN        NaN         NaN     269  
3       NaN        NaN         NaN     269  
4       NaN        NaN         NaN     269

In [4]:
df_mastertable.shape

(147026, 10)

In [5]:
null_percentage = pd.DataFrame(
    (100 * df_mastertable.isna().sum() / df_mastertable.shape[0]).sort_values(ascending=False),
     columns=['Percentage'])

display(null_percentage)
num_null = len(null_percentage[null_percentage.Percentage != 0])
print(f'Number of features with null values: {num_null}')

Percentage
Email SLA         71.451988
Actual AHT        57.937372
Chat SLA          57.931250
Resolution Rate   47.523567
NETRT SLA         32.450043
ResRec SLA        28.720770
Week               0.000000
Skill              0.000000
Case Channel       0.000000
emp_id             0.000000

Number of features with null values: 6


In [6]:
dup = df_mastertable.shape[0] - df_mastertable.drop_duplicates().shape[0]
print(f'There are {dup} duplicate rows')

There are 0 duplicate rows


In [7]:
df_mastertable.columns

Index(['Week', 'Skill', 'Case Channel', 'Resolution Rate', 'NETRT SLA',
       'ResRec SLA', 'Chat SLA', 'Email SLA', 'Actual AHT', 'emp_id'],
      dtype='object')

In [8]:
df_mastertable['Week'] = pd.to_datetime(df_mastertable['Week'])

## Performance Trend

In [9]:
metric_summary = df_mastertable.groupby(['Week', 'Skill']).aggregate(
RR = ('Resolution Rate', 'mean'),
AHT = ('Actual AHT', 'mean')).reset_index()

In [10]:
mk.original_test(metric_summary[metric_summary['Skill'] == "SBG"]['RR'])

Mann_Kendall_Test(trend='increasing', h=True, p=3.503982437536024e-09, z=5.906054428736204, Tau=0.4072164948453608, s=1896.0, var_s=102949.33333333333, slope=0.0014080685556168665, intercept=0.6292984248021826)

In [11]:
mk.original_test(metric_summary[metric_summary['Skill'] == "SBG"]['AHT'])

Mann_Kendall_Test(trend='increasing', h=True, p=3.929168374661174e-06, z=4.615094317431517, Tau=0.41681790683605563, s=689.0, var_s=22223.666666666668, slope=0.08167315735689717, intercept=22.910933617145595)

In [12]:
mk.original_test(metric_summary[metric_summary['Skill'] == "GBG"]['RR'])

Mann_Kendall_Test(trend='increasing', h=True, p=6.563638521583925e-13, z=7.188244728461114, Tau=0.4982456140350877, s=2272.0, var_s=99813.33333333333, slope=0.0023638558836605542, intercept=0.7562673120549254)

In [13]:
mk.original_test(metric_summary[metric_summary['Skill'] == "GBG"]['AHT'])

Mann_Kendall_Test(trend='increasing', h=True, p=0.008550286590018219, z=2.629530483187725, Tau=0.23774954627949182, s=393.0, var_s=22223.666666666668, slope=0.03546367750338897, intercept=21.835799982901698)

Percent Change

In [14]:
df_SBG = metric_summary[metric_summary['Skill'] == "SBG"].reset_index(drop = True)

In [15]:
for i in range(1, len(df_SBG)):
    prev_RR = df_SBG.iloc[i-1, 2]
    current_RR = df_SBG.iloc[i, 2]
    prev_AHT = df_SBG.iloc[i-1, 3]
    current_AHT = df_SBG.iloc[i, 3]
    
    if math.isnan(prev_RR):
        change_RR = None
    else:
        change_RR = ((current_RR - prev_RR)/prev_RR) * 100
    
    df_SBG.at[i,"RR_change"] = change_RR
    
    if math.isnan(prev_AHT):
        change_AHT = None
    else:
        change_AHT = ((current_AHT - prev_AHT)/prev_AHT) * 100
    
    df_SBG.at[i,"AHT_change"] = change_AHT
        

In [ ]:
fig, ax1 = plt.subplots(figsize = (10, 7)) 
    
ax1.plot(df_SBG['Week'],
         df_SBG['RR'],
         color = "orange",
         linewidth = 2,
         label = "RR")
ax1.set_xlabel('Date') 
ax1.set_ylabel('Resolution Rate (Mean)') 

ax2 = ax1.twinx() 
ax2.plot(df_SBG['Week'],
         df_SBG['RR_change'],
         color = "gray",
         alpha = 0.5,
         linewidth = 2,
         linestyle = 'dashed',
         label = "Percent Change")
ax2.set_ylabel('Percent Change in Resolution Rate') 

lines_labels = [ax.get_legend_handles_labels() for ax in fig.axes]
lines, labels = [sum(lol, []) for lol in zip(*lines_labels)]
fig.legend(labels, loc='lower center', ncol=len(labels), bbox_transform=fig.transFigure)
plt.show()

In [ ]:
fig, ax1 = plt.subplots(figsize = (10, 7)) 
    
ax1.plot(df_SBG['Week'],
         df_SBG['AHT'],
         color = "orange",
         linewidth = 2,
         label = "AHT")
ax1.set_xlabel('Date') 
ax1.set_ylabel('Handle Time (Mean)') 

ax2 = ax1.twinx() 
ax2.plot(df_SBG['Week'],
         df_SBG['AHT_change'],
         color = "gray",
         alpha = 0.5,
         linewidth = 2,
         linestyle = 'dashed',
         label = "Percent Change")
ax2.set_ylabel('Percent Change in Handle Time') 

lines_labels = [ax.get_legend_handles_labels() for ax in fig.axes]
lines, labels = [sum(lol, []) for lol in zip(*lines_labels)]
fig.legend(labels, loc='lower center', ncol=len(labels), bbox_transform=fig.transFigure)
plt.show()

In [18]:
mk.original_test(df_SBG['RR_change'])

Mann_Kendall_Test(trend='no trend', h=False, p=0.7253326207806727, z=0.3513408916156687, Tau=0.02456140350877193, s=112.0, var_s=99813.33333333333, slope=0.0037660805116948304, intercept=-0.21053655352949896)

In [19]:
mk.original_test(df_SBG['AHT_change'])

Mann_Kendall_Test(trend='no trend', h=False, p=0.6947779129793568, z=0.3923793886455474, Tau=0.03634085213032581, s=58.0, var_s=21102.666666666668, slope=0.016457019515647434, intercept=-1.2329120268489733)

In [20]:
df_GBG = metric_summary[metric_summary['Skill'] == "GBG"].reset_index(drop = True)

In [21]:
for i in range(1, len(df_GBG)):
    prev_RR = df_GBG.iloc[i-1, 2]
    current_RR = df_GBG.iloc[i, 2]
    prev_AHT = df_GBG.iloc[i-1, 3]
    current_AHT = df_GBG.iloc[i, 3]
    
    if math.isnan(prev_RR):
        change_RR = None
    else:
        change_RR = ((current_RR - prev_RR)/prev_RR) * 100
    
    df_GBG.at[i,"RR_change"] = change_RR
    
    if math.isnan(prev_AHT):
        change_AHT = None
    else:
        change_AHT = ((current_AHT - prev_AHT)/prev_AHT) * 100
    
    df_GBG.at[i,"AHT_change"] = change_AHT
        

In [ ]:
fig, ax1 = plt.subplots(figsize = (10, 7)) 
    
ax1.plot(df_GBG['Week'],
         df_GBG['RR'],
         color = "orange",
         linewidth = 2,
         label = "RR")
ax1.set_xlabel('Date') 
ax1.set_ylabel('Resolution Rate (Mean)') 

ax2 = ax1.twinx() 
ax2.plot(df_GBG['Week'],
         df_GBG['RR_change'],
         color = "gray",
         alpha = 0.5,
         linewidth = 2,
         linestyle = 'dashed',
         label = "Percent Change")
ax2.set_ylabel('Percent Change in Resolution Rate') 

lines_labels = [ax.get_legend_handles_labels() for ax in fig.axes]
lines, labels = [sum(lol, []) for lol in zip(*lines_labels)]
fig.legend(labels, loc='lower center', ncol=len(labels), bbox_transform=fig.transFigure)
plt.show()

In [ ]:
fig, ax1 = plt.subplots(figsize = (10, 7)) 
    
ax1.plot(df_GBG['Week'],
         df_GBG['AHT'],
         color = "orange",
         linewidth = 2,
         label = "AHT")
ax1.set_xlabel('Date') 
ax1.set_ylabel('Handle Time (Mean)') 

ax2 = ax1.twinx() 
ax2.plot(df_GBG['Week'],
         df_GBG['AHT_change'],
         color = "gray",
         alpha = 0.5,
         linewidth = 2,
         linestyle = 'dashed',
         label = "Percent Change")
ax2.set_ylabel('Percent Change in Handle Time') 

lines_labels = [ax.get_legend_handles_labels() for ax in fig.axes]
lines, labels = [sum(lol, []) for lol in zip(*lines_labels)]
fig.legend(labels, loc='lower center', ncol=len(labels), bbox_transform=fig.transFigure)
plt.show()

In [24]:
mk.original_test(df_GBG['RR_change'])

Mann_Kendall_Test(trend='no trend', h=False, p=0.8242310411795755, z=-0.22210641879205095, Tau=-0.015785861358956762, s=-69.0, var_s=93733.66666666667, slope=-0.0045559796751192035, intercept=1.0602850450257355)

In [25]:
mk.original_test(df_GBG['AHT_change'])

Mann_Kendall_Test(trend='no trend', h=False, p=0.9177584197480075, z=0.10325773385409143, Tau=0.010025062656641603, s=16.0, var_s=21102.666666666668, slope=0.007127012465892028, intercept=0.09119990838256709)